In [1]:
import argparse
import json
import os
from collections import OrderedDict
import torch
import csv
#import util
!pip install transformers
!pip install tensorboardX
from transformers import DistilBertTokenizerFast
from transformers import DistilBertForQuestionAnswering
from transformers import AdamW
from tensorboardX import SummaryWriter

from torch.utils.data import DataLoader
from torch.utils.data.sampler import RandomSampler, SequentialSampler
#from args import get_train_test_args

from tqdm import tqdm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 60.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 34.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 124.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 82.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.6/101.6 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 304.5/304.5 kB 15.3 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 3.20.3
    Uninstalling protobuf-3.20.3:
      Successfully uninstalled protobuf-3.20.3


In [2]:
os.chdir("/content/drive/My Drive/robustqa")
!ls

args.py		     datasets_50k.tar.gz  __pycache__  SelfRC.json
convert_to_squad.py  environment.yml	  README.md    train.py
datasets	     ParaphraseRC.json	  save	       util.py


In [3]:
# Import some utility functions
import sys
sys.path.append('/content/drive/My Drive/robustqa')
from util import *

In [4]:
#EDA starter code
import random
from random import shuffle
random.seed(1)

#stop words list
stop_words = ['i', 'me', 'my', 'myself', 'we', 'our',
			'ours', 'ourselves', 'you', 'your', 'yours',
			'yourself', 'yourselves', 'he', 'him', 'his',
			'himself', 'she', 'her', 'hers', 'herself',
			'it', 'its', 'itself', 'they', 'them', 'their',
			'theirs', 'themselves', 'what', 'which', 'who',
			'whom', 'this', 'that', 'these', 'those', 'am',
			'is', 'are', 'was', 'were', 'be', 'been', 'being',
			'have', 'has', 'had', 'having', 'do', 'does', 'did',
			'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or',
			'because', 'as', 'until', 'while', 'of', 'at',
			'by', 'for', 'with', 'about', 'against', 'between',
			'into', 'through', 'during', 'before', 'after',
			'above', 'below', 'to', 'from', 'up', 'down', 'in',
			'out', 'on', 'off', 'over', 'under', 'again',
			'further', 'then', 'once', 'here', 'there', 'when',
			'where', 'why', 'how', 'all', 'any', 'both', 'each',
			'few', 'more', 'most', 'other', 'some', 'such', 'no',
			'nor', 'not', 'only', 'own', 'same', 'so', 'than', 'too',
			'very', 's', 't', 'can', 'will', 'just', 'don',
			'should', 'now', '']

#cleaning up text
import re
def get_only_chars(line):

    clean_line = ""

    line = line.replace("’", "")
    line = line.replace("'", "")
    line = line.replace("-", " ") #replace hyphens with spaces
    line = line.replace("\t", " ")
    line = line.replace("\n", " ")
    line = line.lower()

    for char in line:
        if char in 'qwertyuiopasdfghjklzxcvbnm ':
            clean_line += char
        else:
            clean_line += ' '

    clean_line = re.sub(' +',' ',clean_line) #delete extra spaces
    if clean_line[0] == ' ':
        clean_line = clean_line[1:]
    return clean_line

In [1]:
# Synonym Replacement implementation
import nltk
nltk.download('wordnet')
from nltk.corpus import wordnet

def synonym_replacement(words, n):
	new_words = words.copy()
	random_word_list = list(set([word for word in words if word not in stop_words]))
	random.shuffle(random_word_list)
	num_replaced = 0
	for random_word in random_word_list:
		synonyms = get_synonyms(random_word)
		if len(synonyms) >= 1:
			synonym = random.choice(list(synonyms))
			new_words = [synonym if word == random_word else word for word in new_words]
			#print("replaced", random_word, "with", synonym)
			num_replaced += 1
		if num_replaced >= n: #only replace up to n words
			break

	sentence = ' '.join(new_words)
	new_words = sentence.split(' ')

	return new_words

def get_synonyms(word):
	synonyms = set()
	for syn in wordnet.synsets(word):
		for l in syn.lemmas():
			synonym = l.name().replace("_", " ").replace("-", " ").lower()
			synonym = "".join([char for char in synonym if char in ' qwertyuiopasdfghjklzxcvbnm'])
			synonyms.add(synonym)
	if word in synonyms:
		synonyms.remove(word)
	return list(synonyms)

def eda(sentence, alpha_sr=0.1, num_aug=9):

  sentence = get_only_chars(sentence)
  words = sentence.split(' ')
  words = [word for word in words if word != '']
  num_words = len(words)

  augmented_sentences = []
  num_new_per_technique = num_aug

	#sr
  if (alpha_sr > 0):
    n_sr = max(1, int(alpha_sr*num_words))
    for _ in range(num_new_per_technique):
      a_words = synonym_replacement(words, n_sr)
      augmented_sentences.append(' '.join(a_words))

  augmented_sentences = [get_only_chars(sentence) for sentence in augmented_sentences]
  shuffle(augmented_sentences)

	#trim so that we have the desired number of augmented sentences
  if num_aug >= 1:
    augmented_sentences = augmented_sentences[:num_aug]
  else:
    keep_prob = num_aug / len(augmented_sentences)
    augmented_sentences = [s for s in augmented_sentences if random.uniform(0, 1) < keep_prob]

	#append the original sentence
  augmented_sentences.append(sentence)

  return augmented_sentences

[nltk_data] Downloading package wordnet to /Users/kaiding/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [5]:
get_synonyms('refer')

['consult',
 'have to doe with',
 'look up',
 'denote',
 'bear on',
 'pertain',
 'advert',
 'come to',
 'concern',
 'touch',
 'name',
 'mention',
 'bring up',
 'cite',
 'touch on',
 'relate']

In [16]:
# function to write augmented data to "context" cell of squad format
def write_augmented_data(dataset, alpha_sr, num_aug):
    aug_format = []
    for instance in dataset["data"]:
      aug_context = eda(instance['paragraphs'][0]['context'], alpha_sr, num_aug)
      for context in aug_context:
        aug_instance = {
                "title": instance['title'],
                "paragraphs": [{
                  'context':context,
                  'qas': instance['paragraphs'][0]['qas']
                }]
          }
        aug_format.append(aug_instance)
    return {"data":aug_format}

In [3]:
li = ["- Acid"]
# how to turn list into string
" ".join(li)


'- Acid'

In [17]:
# Augment ood training set and check it works as intended
dataset = json.load(open(f'/content/drive/MyDrive/robustqa/datasets/oodomain_train/duorc.json'))
dataset_aug = write_augmented_data(dataset, 0.1, 9)
dataset_aug

{'data': [{'title': 'The Hunting Party',
   'paragraphs': [{'context': 'relations are strained between cattle baron brandt ruger gene hackman and his wife genus melissa candice bergen when he leaves for a two calendar week hunting trip with some of his wealthy friends mistaking her for a schoolteacher outlaw frank calder king oliver john reed and his band of rustlers and thieve kidnap genus melissa not for redeem but because calder wants to be instruct how to read a record journey by luxurious private train the hunting party engages in debauchery with women matchless of whom ruger sadistically abuses send word that his wife has been make captive ruger arms his friends with high powered rifles to begin a hunt not for animals but for homo calder twice must keep genus melissa from being raped by his homo but finally he overpowers and rapes her himself genus melissa effort to shoot and stab calder and to flee each time in vain she goes on a hunger chance upon but cannot hold out the tempta

In [18]:
#export to json in different locations
def export_to_json(dataset, data_dir, file_name):
    with open(f'{data_dir}/{file_name}.json', 'w') as outfile:
        json.dump(dataset, outfile)

export_to_json(dataset_aug, "/content/drive/MyDrive/robustqa/datasets/oodomain_train", "duorc_augp0.1")

In [9]:
# import existing functions
# Tokenization
# Borrowed existing helper functinos from train.py
def prepare_eval_data(dataset_dict, tokenizer):
    tokenized_examples = tokenizer(dataset_dict['question'],
                                   dataset_dict['context'],
                                   truncation="only_second",
                                   stride=128,
                                   max_length=384,
                                   return_overflowing_tokens=True,
                                   return_offsets_mapping=True,
                                   padding='max_length')
    # Since one example might give us several features if it has a long context, we need a map from a feature to
    # its corresponding example. This key gives us just that.
    sample_mapping = tokenized_examples.pop("overflow_to_sample_mapping")

    # For evaluation, we will need to convert our predictions to substrings of the context, so we keep the
    # corresponding example_id and we will store the offset mappings.
    tokenized_examples["id"] = []
    for i in tqdm(range(len(tokenized_examples["input_ids"]))):
        # Grab the sequence corresponding to that example (to know what is the context and what is the question).
        sequence_ids = tokenized_examples.sequence_ids(i)
        # One example can give several spans, this is the index of the example containing this span of text.
        sample_index = sample_mapping[i]
        tokenized_examples["id"].append(dataset_dict["id"][sample_index])
        # Set to None the offset_mapping that are not part of the context so it's easy to determine if a token
        # position is part of the context or not.
        tokenized_examples["offset_mapping"][i] = [
            (o if sequence_ids[k] == 1 else None)
            for k, o in enumerate(tokenized_examples["offset_mapping"][i])
        ]
    return tokenized_examples

def prepare_train_data(dataset_dict, tokenizer):
    tokenized_examples = tokenizer(dataset_dict['question'],
                                   dataset_dict['context'],
                                   truncation="only_second",
                                   stride=128,
                                   max_length=384,
                                   return_overflowing_tokens=True,
                                   return_offsets_mapping=True,
                                   padding='max_length')
    sample_mapping = tokenized_examples["overflow_to_sample_mapping"]
    offset_mapping = tokenized_examples["offset_mapping"]

    # Let's label those examples!
    tokenized_examples["start_positions"] = []
    tokenized_examples["end_positions"] = []
    tokenized_examples['id'] = []
    inaccurate = 0
    for i, offsets in enumerate(tqdm(offset_mapping)):
        # We will label impossible answers with the index of the CLS token.
        input_ids = tokenized_examples["input_ids"][i]
        cls_index = input_ids.index(tokenizer.cls_token_id)

        # Grab the sequence corresponding to that example (to know what is the context and what is the question).
        sequence_ids = tokenized_examples.sequence_ids(i)

        # One example can give several spans, this is the index of the example containing this span of text.
        sample_index = sample_mapping[i]
        answer = dataset_dict['answer'][sample_index]
        # Start/end character index of the answer in the text.
        # make sure start_
        start_char = answer['answer_start'][0]
        end_char = start_char + len(answer['text'][0])
        tokenized_examples['id'].append(dataset_dict['id'][sample_index])
        # Start token index of the current span in the text.
        token_start_index = 0
        while sequence_ids[token_start_index] != 1:
            token_start_index += 1

        # End token index of the current span in the text.
        token_end_index = len(input_ids) - 1
        while sequence_ids[token_end_index] != 1:
            token_end_index -= 1

        # Detect if the answer is out of the span (in which case this feature is labeled with the CLS index).
        if not (offsets[token_start_index][0] <= start_char and offsets[token_end_index][1] >= end_char):
            tokenized_examples["start_positions"].append(cls_index)
            tokenized_examples["end_positions"].append(cls_index)
        else:
            # Otherwise move the token_start_index and token_end_index to the two ends of the answer.
            # Note: we could go after the last offset if the answer is the last word (edge case).
            while token_start_index < len(offsets) and offsets[token_start_index][0] <= start_char:
                token_start_index += 1
            tokenized_examples["start_positions"].append(token_start_index - 1)
            while offsets[token_end_index][1] >= end_char:
                token_end_index -= 1
            tokenized_examples["end_positions"].append(token_end_index + 1)
            # assertion to check if this checks out
            context = dataset_dict['context'][sample_index]
            offset_st = offsets[tokenized_examples['start_positions'][-1]][0]
            offset_en = offsets[tokenized_examples['end_positions'][-1]][1]
            if context[offset_st : offset_en] != answer['text'][0]:
                inaccurate += 1

    total = len(tokenized_examples['id'])
    print(f"Preprocessing not completely accurate for {inaccurate}/{total} instances")
    return tokenized_examples


def read_and_process(tokenizer, dataset_dict, dir_name, dataset_name, split, recompute=False):
    #TODO: cache this if possible
    cache_path = f'{dir_name}/{dataset_name}_encodings.pt'
    if os.path.exists(cache_path) and not recompute:
        tokenized_examples = util.load_pickle(cache_path)
    else:
        if split=='train':
            tokenized_examples = prepare_train_data(dataset_dict, tokenizer)
        else:
            tokenized_examples = prepare_eval_data(dataset_dict, tokenizer)
        util.save_pickle(tokenized_examples, cache_path)
    return tokenized_examples

def get_dataset(datasets, data_dir, tokenizer, split_name, recompute=False):
    datasets = datasets.split(',')
    dataset_dict = None
    dataset_name=''
    for dataset in datasets:
        dataset_name += f'_{dataset}'
        dataset_dict_curr = util.read_squad(f'{data_dir}/{dataset}')
        dataset_dict = util.merge(dataset_dict, dataset_dict_curr)
    data_encodings = read_and_process(tokenizer, dataset_dict, data_dir, dataset_name, split_name, recompute)
    return util.QADataset(data_encodings, train=(split_name=='train')), dataset_dict

In [10]:
# Train and evaluate functions
import os
from torch.optim import AdamW
from torch.utils.tensorboard import SummaryWriter
from tqdm import tqdm
from collections import OrderedDict
import torch
import util

def save(model, path):
    model.save_pretrained(path)

def evaluate(model, data_loader, data_dict, return_preds=False, split='validation', device='cpu'):
    model.to(device)
    model.eval()
    pred_dict = {}
    all_start_logits = []
    all_end_logits = []
    with torch.no_grad(), tqdm(total=len(data_loader.dataset)) as progress_bar:
        for batch in data_loader:
            # Setup for forward
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            batch_size = len(input_ids)
            outputs = model(input_ids, attention_mask=attention_mask)
            # Forward
            start_logits, end_logits = outputs.start_logits, outputs.end_logits
            # TODO: compute loss

            all_start_logits.append(start_logits)
            all_end_logits.append(end_logits)
            progress_bar.update(batch_size)

    # Get F1 and EM scores
    start_logits = torch.cat(all_start_logits).cpu().numpy()
    end_logits = torch.cat(all_end_logits).cpu().numpy()
    preds = util.postprocess_qa_predictions(data_dict,
                                             data_loader.dataset.encodings,
                                             (start_logits, end_logits))
    if split == 'validation' or 'test':
        results = util.eval_dicts(data_dict, preds)
        results_list = [('F1', results['F1']),
                        ('EM', results['EM'])]
    results = OrderedDict(results_list)
    if return_preds:
        return preds, results
    return results

def train(model, train_dataloader, eval_dataloader, val_dict, lr, num_epochs, device, eval_every,
          num_visuals, save_dir, visualize_predictions=False):
    model.to(device)
    optim = AdamW(model.parameters(), lr=lr)
    global_idx = 0
    best_scores = {'F1': -1.0, 'EM': -1.0}
    tbx = SummaryWriter(save_dir)

    for epoch_num in range(num_epochs):
        print(f'Epoch: {epoch_num}')
        with torch.enable_grad(), tqdm(total=len(train_dataloader.dataset)) as progress_bar:
            for batch in train_dataloader:
                optim.zero_grad()
                model.train()
                input_ids = batch['input_ids'].to(device)
                attention_mask = batch['attention_mask'].to(device)
                start_positions = batch['start_positions'].to(device)
                end_positions = batch['end_positions'].to(device)
                outputs = model(input_ids, attention_mask=attention_mask,
                                start_positions=start_positions,
                                end_positions=end_positions)
                loss = outputs[0]
                loss.backward()
                optim.step()
                progress_bar.update(len(input_ids))
                progress_bar.set_postfix(epoch=epoch_num, NLL=loss.item())
                tbx.add_scalar('train/NLL', loss.item(), global_idx)
                if (global_idx % eval_every) == 0:
                    print(f'Evaluating at step {global_idx}...')
                    preds, curr_score = evaluate(model, eval_dataloader, val_dict, return_preds=True, device=device)
                    results_str = ', '.join(f'{k}: {v:05.2f}' for k, v in curr_score.items())
                    print('Visualizing in TensorBoard...')
                    for k, v in curr_score.items():
                        tbx.add_scalar(f'val/{k}', v, global_idx)
                    print(f'Eval {results_str}')
                    if visualize_predictions:
                        util.visualize(tbx,
                                       pred_dict=preds,
                                       gold_dict=val_dict,
                                       step=global_idx,
                                       split='val',
                                       num_visuals=num_visuals)
                    if curr_score['F1'] >= best_scores['F1']:
                        best_scores = curr_score
                        save(model, os.path.join(save_dir, 'checkpoint'))
                global_idx += 1
    return best_scores

In [19]:
# Tokenize
import util
util.set_seed(42)

# In-domain train and val data
tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased')
train_dataset, _ = get_dataset("duorc_augp0.1.json","/content/drive/MyDrive/robustqa/datasets/oodomain_train", tokenizer, 'train')
train_loader = DataLoader(train_dataset,
                          batch_size=16,
                          sampler=RandomSampler(train_dataset))

100%|██████████| 21535/21535 [00:00<00:00, 45282.08it/s]


Preprocessing not completely accurate for 4479/21535 instances


In [21]:
val_dataset, val_dict = get_dataset("duorc.json","/content/drive/MyDrive/robustqa/datasets/oodomain_val", tokenizer, 'val')
val_loader = DataLoader(val_dataset,
                        batch_size=16,
                        sampler=SequentialSampler(val_dataset))

In [22]:
# Train pretained baseline 2 model on augmented ood data
save_dir = "/content/drive/MyDrive/robustqa/save"
if not os.path.exists(save_dir):
  os.makedirs(save_dir)
save_dir = util.get_save_dir(save_dir, "multitask_distilbert_augp0.1")
log = util.get_logger(save_dir, 'log_train')

device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
model = DistilBertForQuestionAnswering.from_pretrained('/content/drive/MyDrive/robustqa/save/multitask_distilbert_baseline2/checkpoint')
best_scores = train(model,train_loader, val_loader, val_dict, lr=3e-5, num_epochs=3, device=device, eval_every=2000,
          num_visuals=10, save_dir=save_dir, visualize_predictions=False)

Epoch: 0


  0%|          | 16/21535 [00:03<1:14:53,  4.79it/s, NLL=4.05, epoch=0]

Evaluating at step 0...



100%|██████████| 25712/25712 [01:04<00:00, 398.67it/s]

100%|██████████| 5165/5165 [00:07<00:00, 686.67it/s]


Visualizing in TensorBoard...
Eval F1: 39.99, EM: 25.96


...

 97%|█████████▋| 20944/21535 [02:56<00:04, 118.72it/s, NLL=0.737, epoch=2]

Evaluating at step 4000...



100%|██████████| 25712/25712 [01:04<00:00, 398.85it/s]

 97%|█████████▋| 20960/21535 [04:10<13:11,  1.38s/it, NLL=0.944, epoch=2]

Visualizing in TensorBoard...
Eval F1: 20.40, EM: 09.02


100%|██████████| 21535/21535 [04:14<00:00, 84.49it/s, NLL=0.974, epoch=2] 


In [24]:
# Evaluate on ood test set
model2 = DistilBertForQuestionAnswering.from_pretrained('/content/drive/MyDrive/robustqa/save/multitask_distilbert_augp0.1-01/checkpoint')
eval_dataset, eval_dict = get_dataset("duorc.json",
                                      "/content/drive/MyDrive/robustqa/datasets/oodomain_test",
                                      tokenizer, "test")
eval_loader = DataLoader(eval_dataset,
                        batch_size=16,
                        sampler=SequentialSampler(eval_dataset))
eval_preds, eval_scores = evaluate(model2, eval_loader,
                                   eval_dict,
                                   return_preds=True,
                                   split='test',
                                   device=device)
results_str = ', '.join(f'{k}: {v:05.2f}' for k, v in eval_scores.items())
print(f'Eval {results_str}')

100%|██████████| 57046/57046 [01:26<00:00, 657.30it/s]


Eval F1: 42.10, EM: 27.79


In [ ]:
def prepare_train_data(dataset_dict, tokenizer):
    tokenized_examples = tokenizer(dataset_dict['question'],
                                   dataset_dict['context'],
                                   truncation="only_second",
                                   stride=128,
                                   max_length=384,
                                   return_overflowing_tokens=True,
                                   return_offsets_mapping=True,
                                   padding='max_length')
    sample_mapping = tokenized_examples["overflow_to_sample_mapping"]
    offset_mapping = tokenized_examples["offset_mapping"]

    tokenized_examples["start_positions"] = []
    tokenized_examples["end_positions"] = []
    tokenized_examples['id'] = []
    # check tokenized_examples number of instances
    print(f"Number of instances: {len(tokenized_examples['input_ids'])}")
    # check dataset_dict number of instances
    print(f"Number of instances: {len(dataset_dict['id'])}")
    # check length of offset mapping
    print(f"Length of offset mapping: {len(offset_mapping)}")
    inaccurate = 0
    for i, offsets in enumerate(tqdm(offset_mapping)):
        try:
            input_ids = tokenized_examples["input_ids"][i]
            cls_index = input_ids.index(tokenizer.cls_token_id)

            sequence_ids = tokenized_examples.sequence_ids(i)

            sample_index = sample_mapping[i]
            answer = dataset_dict['answer'][sample_index]
            start_char = answer['answer_start'][0]
            end_char = start_char + len(answer['text'][0])
            tokenized_examples['id'].append(dataset_dict['id'][sample_index])

            token_start_index = 0
            while sequence_ids[token_start_index] != 1:
                token_start_index += 1

            token_end_index = len(input_ids) - 1
            while sequence_ids[token_end_index] != 1:
                token_end_index -= 1

            if not (offsets[token_start_index][0] <= start_char and offsets[token_end_index][1] >= end_char):
                tokenized_examples["start_positions"].append(cls_index)
                tokenized_examples["end_positions"].append(cls_index)
            else:
                while token_start_index < len(offsets) and offsets[token_start_index][0] <= start_char:
                    token_start_index += 1
                tokenized_examples["start_positions"].append(token_start_index - 1)
                while offsets[token_end_index][1] >= end_char:
                    token_end_index -= 1
                tokenized_examples["end_positions"].append(token_end_index + 1)

                context = dataset_dict['context'][sample_index]
                offset_st = offsets[tokenized_examples['start_positions'][-1]][0]
                offset_en = offsets[tokenized_examples['end_positions'][-1]][1]
                if context[offset_st : offset_en] != answer['text'][0]:
                    inaccurate += 1
        except IndexError as ie:
            print(f"Skipping due to IndexError at index {i}: {ie}")
            # also remove index i from tokenized examples
            for key in tokenized_examples:
                tokenized_examples[key].pop(i)
            continue

    total = len(tokenized_examples['id'])
    print(f"Preprocessing not completely accurate for {inaccurate}/{total} instances")
    return tokenized_examples

In [ ]:
def prepare_train_data(dataset_dict, tokenizer):
    tokenized_examples = tokenizer(dataset_dict['question'],
                                   dataset_dict['context'],
                                   truncation="only_second",
                                   stride=128,
                                   max_length=384,
                                   return_overflowing_tokens=True,
                                   return_offsets_mapping=True,
                                   padding='max_length')
    sample_mapping = tokenized_examples.pop("overflow_to_sample_mapping")
    offset_mapping = tokenized_examples.pop("offset_mapping")

    # Initialize new dictionary for the modified dataset
    modified_dataset_dict = {}
    for key in dataset_dict.keys():
        modified_dataset_dict[key] = []
    
    tokenized_examples["start_positions"] = []
    tokenized_examples["end_positions"] = []
    tokenized_examples['id'] = []

    inaccurate = 0
    for i, offsets in enumerate(tqdm(offset_mapping)):
        try:
            input_ids = tokenized_examples["input_ids"][i]
            cls_index = input_ids.index(tokenizer.cls_token_id)
            sequence_ids = tokenized_examples.sequence_ids(i)

            sample_index = sample_mapping[i]
            answer = dataset_dict['answer'][sample_index]
            start_char = answer['answer_start'][0]
            end_char = start_char + len(answer['text'][0])
            tokenized_examples['id'].append(dataset_dict['id'][sample_index])

            token_start_index = 0
            while sequence_ids[token_start_index] != 1:
                token_start_index += 1

            token_end_index = len(input_ids) - 1
            while sequence_ids[token_end_index] != 1:
                token_end_index -= 1

            if not (offsets[token_start_index][0] <= start_char and offsets[token_end_index][1] >= end_char):
                tokenized_examples["start_positions"].append(cls_index)
                tokenized_examples["end_positions"].append(cls_index)
            else:
                while token_start_index < len(offsets) and offsets[token_start_index][0] <= start_char:
                    token_start_index += 1
                tokenized_examples["start_positions"].append(token_start_index - 1)
                while offsets[token_end_index][1] >= end_char:
                    token_end_index -= 1
                tokenized_examples["end_positions"].append(token_end_index + 1)

                context = dataset_dict['context'][sample_index]
                offset_st = offsets[tokenized_examples['start_positions'][-1]][0]
                offset_en = offsets[tokenized_examples['end_positions'][-1]][1]
                if context[offset_st : offset_en] != answer['text'][0]:
                    inaccurate += 1

            # Append the values to the new dictionaries
            for key in dataset_dict.keys():
                modified_dataset_dict[key].append(dataset_dict[key][sample_index])

        except IndexError as ie:
            print(f"Skipping due to IndexError at index {i}: {ie}")
            # remove the index from tensor tokenized_examples
            

            
            
            #for key in tokenized_examples.keys():
            #    print(f"Removing index {i} from {key}")
            #    tokenized_examples[key].pop(i)
            continue

    total = len(tokenized_examples['id'])

    print(f"Preprocessing not completely accurate for {inaccurate}/{total} instances")
    return modified_tokenized_examples